In [ ]:
!pip install -U spacy

# Imports

In [ ]:
import spacy
from spacy.training import Example, offsets_to_biluo_tags
from transformers import AutoTokenizer, AutoModel
import torch
import random
import pandas as pd
import json

# Configurar o spaCy e o modelo BERT

In [ ]:
spacy.prefer_gpu()
nlp = spacy.blank('pt')

# Carregar dados

In [ ]:
with open('/content/drive/MyDrive/resultados.json', 'r',  encoding='utf-8') as arquivo:
    try:
        data = json.load(arquivo)
    except json.JSONDecodeError:
        data = []

# Converter dados para DataFrame
df = pd.DataFrame(data)

# Função para ajustar os deslocamentos das entidades

In [ ]:
def adjust_offsets(tokens, entities):
    adjusted_entities = []
    for start, end, label in entities:
        adjusted_start = None
        adjusted_end = None
        for i, token in enumerate(tokens):
            if start >= token[1] and start < token[2]:
                adjusted_start = i
            if end > token[1] and end <= token[2]:
                adjusted_end = i
        if adjusted_start is not None and adjusted_end is not None:
            adjusted_entities.append([tokens[adjusted_start][1], tokens[adjusted_end][2], label])
    return adjusted_entities

# Função para validar as anotações

In [ ]:
def validate_annotations(text, corrected_entities):
    doc = nlp(text)
    biluo_tags = offsets_to_biluo_tags(doc, corrected_entities)
    if None in biluo_tags:
        print(f"Misalignment detected in text: {text}")
        print(f"Entities: {corrected_entities}")
    else:
        print(f"Validated BILUO Tags: {biluo_tags}")

In [ ]:
# Ajustar e validar as anotações
for index, row in df.iterrows():
    text = row[0]
    entities = row[1]['entities']
    doc = nlp(text)
    tokens = [(token.text, token.idx, token.idx + len(token.text)) for token in doc]

    corrected_entities = adjust_offsets(tokens, entities)

    # Validar as anotações ajustadas
    validate_annotations(text, corrected_entities)

    # Atualizar o DataFrame com as anotações corrigidas
    df.at[index, 1] = {'entities': corrected_entities}

In [ ]:
# Preparar dados de treinamento
TRAIN_DATA = []
for _, row in df.iterrows():
    try:
        text = row[0].strip()  # Usando strip() para remover quebras de linha e espaços desnecessários
        entities = row[1]  # Já é um dicionário, então use diretamente

        # Verifique se o dicionário tem a chave 'entities'
        if isinstance(entities, dict) and 'entities' in entities:
            TRAIN_DATA.append((text, {"entities": entities["entities"]}))
        else:
            raise ValueError("O formato das entidades está incorreto")

    except Exception as e:
        print(f"Erro ao processar a linha: {e}")
        print(f"Dados da linha: Texto: {text}, Entidades: {entities}")

# Carregar o tokenizer e o modelo BERT para embeddings
tokenizer = AutoTokenizer.from_pretrained('neuralmind/bert-base-portuguese-cased')
model = AutoModel.from_pretrained('neuralmind/bert-base-portuguese-cased')

# Definir o componente personalizado para embeddings BERT

In [ ]:
@spacy.Language.component("astra_ner")
def embed_with_bert(doc):
    inputs = tokenizer(doc.text, return_tensors="pt", padding=True, truncation=True, max_length=512)
    with torch.no_grad():
        outputs = model(**inputs)
        encoded_text = outputs.last_hidden_state.mean(dim=1)  # Usar a média dos embeddings dos tokens
    doc.user_data["bert_embedding"] = encoded_text.cpu().numpy()
    return doc

# Adicionar o componente BERT ao pipeline do spaCy
if "transformer" not in nlp.pipe_names:
    nlp.add_pipe("astra_ner", last=True)

# Função para treinar o reconhecedor de entidades
def train_entity_recognizer(nlp, train_data):
    if "ner" not in nlp.pipe_names:
        ner = nlp.add_pipe("ner", last=True)
    else:
        ner = nlp.get_pipe("ner")

    for _, annotations in train_data:
        for ent in annotations['entities']:
            ner.add_label(ent[2])

    optimizer = nlp.begin_training()
    for itn in range(10):
        random.shuffle(train_data)
        losses = {}
        for text, annotations in train_data:
            doc = nlp.make_doc(text)
            biluo_tags = offsets_to_biluo_tags(doc, annotations['entities'])

            # Verificar alinhamento das anotações
            if None in biluo_tags:
                print(f"Misalignment detected in text: {text}")
                continue

            example = Example.from_dict(doc, annotations)
            nlp.update([example], drop=0.5, sgd=optimizer, losses=losses)
        print(losses)

# Treinar o modelo

In [ ]:

# Treinar o modelo
train_entity_recognizer(nlp, TRAIN_DATA)

# Salvar o modelo treinado
nlp.to_disk("/content/treinado_modelo")

# Carregar o modelo treinado
nlp = spacy.load("/content/treinado_modelo")

# Usar o modelo para previsões
texto = "GR16031-00542"
doc = nlp(texto)

# Imprimir entidades detectadas
for ent in doc.ents:
    print(f"Texto: {ent.text}, Tipo: {ent.label_}")

Streaming output truncated to the last 5000 lines.
Validated BILUO Tags: ['U-HORA', 'O', 'U-HORA', 'O', 'U-HORA', 'U-GR', 'O', 'O', 'U-HORA', 'O', 'O', 'U-HORA', 'O', 'O', 'O', 'O', 'U-GR', 'U-HORA', 'U-GR', 'U-TURNO', 'U-TURNO', 'U-HORA', 'U-GR', 'U-GR', 'U-HORA', 'U-HORA', 'O', 'O', 'U-GR', 'U-HORA', 'O', 'O', 'U-GR', 'U-GR', 'O', 'U-HORA', 'U-HORA', 'O', 'O', 'U-HORA', 'U-HORA', 'U-HORA', 'U-HORA', 'U-GR', 'O', 'U-GR', 'U-HORA', 'U-HORA', 'O', 'O', 'U-GR', 'U-HORA', 'O', 'O', 'O', 'U-HORA', 'U-GR', 'O', 'O', 'U-GR', 'U-HORA', 'O', 'U-HORA', 'O', 'O', 'U-HORA', 'O', 'O', 'U-HORA', 'U-HORA', 'U-HORA', 'U-HORA', 'U-GR', 'U-HORA', 'U-HORA', 'U-HORA', 'U-HORA', 'O', 'U-HORA', 'U-GR', 'O', 'O', 'U-HORA', 'U-HORA', 'O', 'U-GR', 'O', 'U-TURNO', 'U-GR', 'U-HORA', 'U-TURNO', 'U-HORA', 'O', 'O', 'U-HORA', 'U-TURNO', 'U-HORA', 'O', 'O', 'U-HORA', 'O', 'O', 'O', 'U-TURNO', 'O', 'O', 'U-TURNO', 'O', 'O', 'U-GR', 'U-TURNO', 'O', 'O', 'U-HORA', 'U-HORA', 'O']
Validated BILUO Tags: ['U-GR', 'U-GR', 